Etapas procesamiento:
- Molienda: 4 equipos cada uno con 3000 kg/hr y merma 0.05
- Prensado: 6 equipos cada uno con 2500 kg/hr y merma 0.15
- Clarificacion: 2 equipos cada uno con 5000 kg/hr y merma 0.35

**SIMULACION**

In [1]:
import math

In [2]:
#fucnion que convierte el diccionario de los lotes que compro en un diccionario de camiones que llegan
#"CamionX"=[tipo uva,kg,calidad,tiempo llegada, tiempo en molienda, tiempo en prensado, tiempo en clarificacion]
def generar_camiones(dicc_lotes):
    dicc_camiones={}
    j=1
    for i in dicc_lotes.values():
        tipo_uva=i[0]
        kg=i[1]
        calidad=i[2]
        tiempo_llegada=i[3]
        tcola=0 #4
        tsmolienda=0 #5
        tbmolienda=0 #6
        tsprensado=0 #7
        tbprensado=0 #8
        tsclarificacion=0 #9
        tbclarificacion=0 #10
        tiempo_fuera=0 #11
        dicc_camiones["CAMION{}".format(j)]=[tipo_uva,kg,calidad,tiempo_llegada,tcola,tsmolienda,tbmolienda,tsprensado,tbprensado,tsclarificacion,tbclarificacion,tiempo_fuera]
        j+=1
    print("INFO CAMIONES: tipo de uva, kg, calidad, tllegada, t en cola, t en molienda,t bloqueado en molienda, t en prensado,t bloqueado en prensado, t en clarif,t bloqueado en clarif, tiempo fuera")
    print(dicc_camiones)
    return dicc_camiones

In [3]:
#funcion que genera diccionarios de los tiempos de salida de los equipos en cada etapa
#y diccionarios de los estados de los equipos en cada etapa
def generar_molienda(equipos):
    tiempos_molienda={}
    estados_molienda={}
    for i in range(equipos):
        tiempos_molienda["TSM{}".format(i+1)]=math.inf
        estados_molienda["M{}".format(i+1)]=[0,0]
    print(tiempos_molienda,estados_molienda)
    return tiempos_molienda,estados_molienda
def generar_prensado(equipos):
    tiempos_prensado={}
    estados_prensado={}
    for i in range(equipos):
        tiempos_prensado["TSP{}".format(i+1)]=math.inf
        estados_prensado["P{}".format(i+1)]=[0,0]
    print(tiempos_prensado,estados_prensado)
    return tiempos_prensado,estados_prensado
def generar_clarificacion(equipos):
    tiempos_clarificacion={}
    estados_clarificacion={}
    for i in range(equipos):
        tiempos_clarificacion["TSC{}".format(i+1)]=math.inf
        estados_clarificacion["C{}".format(i+1)]=[0,0]
    print(tiempos_clarificacion,estados_clarificacion)
    return tiempos_clarificacion,estados_clarificacion

In [4]:
#funcion que decide el prox evento a ocurrir
def prox_evento(dicc_camiones,tiempos_molienda,tiempos_prensado,tiempos_clarificacion):
    tiempos=[]
    for i in dicc_camiones:
        tiempos.append([i,dicc_camiones[i][3]])
    for i in tiempos_molienda:
        tiempos.append([i,tiempos_molienda[i]])
    for i in tiempos_prensado:
        tiempos.append([i,tiempos_prensado[i]])
    for i in tiempos_clarificacion:
        tiempos.append([i,tiempos_clarificacion[i]])
    tipo_evento=math.inf
    tiempo_evento=math.inf
    for i in tiempos:
        if i[1]<tiempo_evento:
            tipo_evento=i[0]
            tiempo_evento=i[1]
    print(tiempos)
    print("El evento {} ocurre a las {} horas".format(tipo_evento,tiempo_evento))
    return tipo_evento,tiempo_evento

In [5]:
def llegada(T,tipo_evento,dicc_camiones,tiempos_molienda,estados_molienda,tasa_molienda,COLA):
    #rescato info del camion
    #si es una llegada, tipo_evento sera el id de un camion
    tipo_uva=dicc_camiones[tipo_evento][0]
    kg=dicc_camiones[tipo_evento][1]
    calidad=dicc_camiones[tipo_evento][2]
    tiempo_fuera=dicc_camiones[tipo_evento][3]
    dicc_camiones[tipo_evento][3]=math.inf #actualizo el tiempo de llegada del camion a infinito
    dicc_camiones[tipo_evento][11]=T #actualizo el tiempo que lleva fuera la uva
    print("----> Llega el camion {} a las {} horas con tipo uva {}, {} kg, calidad {}.".format(tipo_evento,T,tipo_uva,kg,calidad))
    #lo asigno a algun equipo molienda
    equipo_asignado=0
    #reviso los equipos de molienda y si encuentro uno desocupado se lo asigno
    for i in estados_molienda:
        if estados_molienda[i][0]==0:
            equipo_asignado=i
            estados_molienda[i]=[1,tipo_evento]
            tiempo_salida=(kg/tasa_molienda)
            tiempos_molienda["TSM{}".format(equipo_asignado[1])]=T+tiempo_salida
            dicc_camiones[tipo_evento][5]=tiempo_salida #tiempo que demora la molienda de este camion
            print("Se asigna al equipo {} de molienda. Saldrá en {} horas más.".format(equipo_asignado,tiempo_salida))
            print(dicc_camiones)
            print(estados_molienda)
            print(tiempos_molienda)
            break
    #si estan todos ocupados lo asigno a la cola
    if equipo_asignado==0:
        print("Todos los equipos de molienda estan ocupados, se agrega a la cola a las {} horas".format(T))
        COLA.append([tipo_evento,T])
        print("COLA: {}".format(COLA))

In [6]:
def salida_molienda(T,tipo_evento,dicc_camiones,tiempos_molienda,estados_molienda,tasa_molienda,merma,tiempos_prensado,estados_prensado,tasa_prensado,COLA):
    #si es salida, tipo de evento sera TSMx Ej "TSM1"
    #rescato y actualizo info del camion
    camion=estados_molienda[tipo_evento[2:]][1] #camion que esta saliendo de molienda Ej "CAMION1"
    equipo=tipo_evento[2:]
    tipo_uva=dicc_camiones[camion][0]
    dicc_camiones[camion][1]=dicc_camiones[camion][1]*(1-merma) #merma que se produce en molienda
    kg=dicc_camiones[camion][1]
    calidad=dicc_camiones[camion][2]
    dicc_camiones[camion][11]=T #actualizo el tiempo que lleva fuera la uva
    print("<---- Sale camion {} de equipo {} MOLIENDA a las {} horas con uva tipo {}, {} kg, calidad {}".format(camion,equipo,T,tipo_uva,kg,calidad))
    #ver si prensado esta desocupado
    equipo_asignado=0 
    for i in estados_prensado:
        if estados_prensado[i][0]==0:
            equipo_asignado=i #Ej "P1"
            print(equipo_asignado)
            estados_prensado[i]=[1,camion] #Ej [1,"CAMION1"]
            tiempo_salida=(kg/tasa_prensado)
            tiempos_prensado["TSP{}".format(equipo_asignado[1])]=T+tiempo_salida
            dicc_camiones[camion][7]=tiempo_salida
            print("Se asigna al equipo {} de prensado. Saldrá en {} horas más.".format(equipo_asignado,tiempo_salida))
            print(dicc_camiones)
            print(estados_prensado)
            print(tiempos_prensado)
            break
    #si no hay ningun equipo prensado desocupado
    if equipo_asignado==0:
        estados_molienda[tipo_evento[2:]][0]=2 
        tiempos_molienda[tipo_evento]=math.inf
        print("No hay ningun equipo de prensado desocupado. Se bloquea")
    #revisar cola
    else:
        if len(COLA)==0: #si no hay camiones en cola
            estados_molienda[tipo_evento[2:]]=[0,0] #Ej "M1"=[0,0]
            tiempos_molienda[tipo_evento]=math.inf #Ej "TSM1"=inf
            print("No hay camiones esperando en cola")
        else: #si hay camiones en cola entra el primero
            camion=COLA[0][0] #Ej "CAMION 1"
            estados_molienda[tipo_evento[2:]]=[1,camion] #Ej "M1"=[1,"CAMION 1"]
            equipo=tipo_evento[2:]
            kg=dicc_camiones[camion][1]
            tiempo_salida=(kg/tasa_molienda)
            tiempos_molienda[tipo_evento]=T+tiempo_salida
            dicc_camiones[camion][4]=T-(COLA[0][1]) #tiempo que estuvo en cola
            dicc_camiones[camion][5]=tiempo_salida
            COLA.pop(0)
            print("Entra el primer camion de la cola al equipo {} de molienda. Saldrá en {} horas más.".format(equipo,tiempo_salida))
            print(dicc_camiones)
            print(estados_molienda)
            print(tiempos_molienda)
            
            
            
            

In [7]:
def salida_prensado(T,tipo_evento,dicc_camiones,tiempos_molienda,estados_molienda,tiempos_prensado,estados_prensado,tasa_prensado,merma,tiempos_clarificacion,estados_clarificacion,tasa_clarificacion):
    #rescato y actualizo info del camion
    camion=estados_prensado[tipo_evento[2:]][1] #camion que esta saliendo de prensado Ej "CAMION1"
    equipo=tipo_evento[2:]
    tipo_uva=dicc_camiones[camion][0]
    dicc_camiones[camion][1]=dicc_camiones[camion][1]*(1-merma) #merma que se produce en molienda
    kg=dicc_camiones[camion][1]
    calidad=dicc_camiones[camion][2]
    dicc_camiones[camion][11]=T #actualizo el tiempo que lleva fuera la uva
    print("<---- Sale camion {} de equipo {} PRENSADO a las {} horas con uva tipo {}, {} kg, calidad {}".format(camion,equipo,T,tipo_uva,kg,calidad))

    #ver si clarificacion esta desocupado
    equipo_asignado=0
    for i in estados_clarificacion:
        if estados_clarificacion[i][0]==0:
            equipo_asignado=i 
            estados_clarificacion[i]=[1,camion]
            tiempo_salida=(kg/tasa_clarificacion)
            tiempos_clarificacion["TSC{}".format(equipo_asignado[1])]=T+tiempo_salida
            dicc_camiones[camion][9]=tiempo_salida
            print("Se asigna al equipo {} de clarificacion. Saldrá en {} horas más.".format(equipo_asignado,tiempo_salida))
            print(dicc_camiones)
            print(estados_clarificacion)
            print(tiempos_clarificacion)
            break
    #si no hay ningun equipo prensado desocupado
    if equipo_asignado==0:
        estados_prensado[tipo_evento[2:]][0]=2 
        tiempos_prensado[tipo_evento]=math.inf
        print("No hay ningun equipo de clarificacion desocupado. Se bloquea")
    #revisar bloqueados
    else:
        tiempo_min=math.inf
        equipo_min=0
        #reviso todos los equipos de molienda bloqueados
        for i in estados_molienda:
            if estados_molienda[i][0]==2:
                camion=estados_molienda[i][1] #camion que esta en el equipo bloqueado
                tiempo=dicc_camiones[camion][11] #tiempo en que habia terminado la molienda
                if tiempo<tiempo_min: 
                    tiempo_min=tiempo 
                    equipo_min=i #obtengo el equipo de molienda bloqueado que habia terminado antes
        print("vemos si hay equipos en molienda bloqueados")
        print(estados_molienda)
        print(tiempos_molienda)
                    
        if equipo_min==0:
            print("no hay equipos de molienda bloqueados")
            estados_prensado[tipo_evento[2:]]=[0,0] #Ej "P1"=[0,0]
            tiempos_prensado[tipo_evento]=math.inf #Ej "TSP1"=inf
        else:
            camion=estados_molienda[equipo_min][1]
            print("camion minimo: {}".format(camion))
            kg=dicc_camiones[camion][1]
            tiempo_salida=(kg/tasa_prensado)
            estados_prensado[tipo_evento[2:]]=[1,camion]
            tiempos_prensado[tipo_evento]=T+tiempo_salida
            tiempo_bloqueado=T-dicc_camiones[camion][5] #tiempo que estuvo bloqueado
            dicc_camiones[camion][6]=tiempo_bloqueado
            dicc_camiones[camion][7]=tiempo_salida
            estados_molienda[equipo_min]=[0,0]
            tiempos_molienda["TSM{}".format(equipo_min[1])]=math.inf
            print("Se desbloquea el equipo {} de molienda. Estuvo bloqueado {} horas ".format(equipo_min,tiempo_bloqueado))
            print("Entra al equipo {} de prensado. Saldra en {} horas mas".format(tipo_evento[2:],tiempo_salida))
            print(dicc_camiones)
            print(estados_prensado)
            print(tiempos_prensado)
            
        

In [8]:
def salida_clarificacion(T,tipo_evento,dicc_camiones,tiempos_prensado,estados_prensado,tiempos_clarificacion,estados_clarificacion,tasa_clarificacion,merma):
    #rescato y actualizo info del camion
    camion=estados_clarificacion[tipo_evento[2:]][1] #camion que esta saliendo de clarificacion Ej "CAMION1"
    equipo=tipo_evento[2:]
    tipo_uva=dicc_camiones[camion][0]
    dicc_camiones[camion][1]=dicc_camiones[camion][1]*(1-merma) #merma que se produce en clarificacion
    kg=dicc_camiones[camion][1]
    calidad=dicc_camiones[camion][2]
    dicc_camiones[camion][11]=T #actualizo el tiempo que lleva fuera la uva
    print("<---- Sale camion {} de equipo {} CLARIFICACION a las {} horas con uva tipo {}, {} kg, calidad {}".format(camion,equipo,T,tipo_uva,kg,calidad))


    #revisar bloqueados
    tiempo_min=math.inf
    equipo_min=0
    #reviso todos los equipos de prensado bloqueados
    for i in estados_prensado:
        if estados_prensado[i][0]==2:
            camion=estados_prensado[i][1] #camion que esta en el equipo bloqueado
            tiempo=dicc_camiones[camion][11] #tiempo en que habia terminado el prensado
            if tiempo<tiempo_min: 
                tiempo_min=tiempo 
                equipo_min=i #obtengo el equipo de prensado bloqueado que habia terminado antes
    print("vemos si hay equipos en prensado bloqueados")
    print(estados_prensado)
    print(tiempos_prensado)

    if equipo_min==0:
        print("no hay equipos de prensado bloqueados")
        estados_clarificacion[tipo_evento[2:]]=[0,0] #Ej "P1"=[0,0]
        tiempos_clarificacion[tipo_evento]=math.inf #Ej "TSP1"=inf
    else:
        camion=estados_prensado[equipo_min][1]
        print("camion minimo: {}".format(camion))
        kg=dicc_camiones[camion][1]
        tiempo_salida=(kg/tasa_clarificacion)
        estados_clarificacion[tipo_evento[2:]]=[1,camion]
        tiempos_clarificacion[tipo_evento]=T+tiempo_salida
        tiempo_bloqueado=T-dicc_camiones[camion][7] #tiempo que estuvo bloqueado
        dicc_camiones[camion][8]=tiempo_bloqueado
        dicc_camiones[camion][9]=tiempo_salida
        estados_prensado[equipo_min]=[0,0]
        tiempos_prensado["TSM{}".format(equipo_min[1])]=math.inf
        print("Se desbloquea el equipo {} de prensado. Estuvo bloqueado {} horas ".format(equipo_min,tiempo_bloqueado))
        print("Entra al equipo {} de clarificacion. Saldra en {} horas mas".format(tipo_evento[2:],tiempo_salida))
        print(dicc_camiones)
        print(estados_clarificacion)
        print(tiempos_clarificacion)

        

In [9]:
#input:
#- dicc_lotes: diccionario de los lotes comprados -> "loteX"=[tipo uva, kg, calidad, tiempo llegada]
#- equipos1: numero de equipos de molienda
#- tasa1: tasa de servicio de molienda (kg/hr)
#- equipos2: numero de equipos de prensado
#- tasa2: tasa de servicio de prensado (kg/hr)
#- equipos3: numero de equipos de clarificacion
#- tasa3: tasa de servicio de clarificacion (kg/hr)

def Simular_procesamiento(dicc_lotes,equipos1,tasa1,merma1,equipos2,tasa2,merma2,equipos3,tasa3,merma3):
    T=0
    dicc_camiones=generar_camiones(dicc_lotes)
    tiempos_molienda,estados_molienda=generar_molienda(equipos1)
    tiempos_prensado,estados_prensado=generar_prensado(equipos2)
    tiempos_clarificacion,estados_clarificacion=generar_clarificacion(equipos3)
    COLA=[]
    tipo_evento,tiempo_evento=prox_evento(dicc_camiones,tiempos_molienda,tiempos_prensado,tiempos_clarificacion)
    while tiempo_evento!=math.inf:
        T=tiempo_evento
        #si es llegada
        if tipo_evento[0]=="C":
            llegada(T,tipo_evento,dicc_camiones,tiempos_molienda,estados_molienda,tasa1,COLA)
        #si es salida
        elif 'M' in tipo_evento:
            salida_molienda(T,tipo_evento,dicc_camiones,tiempos_molienda,estados_molienda,tasa1,merma1,tiempos_prensado,estados_prensado,tasa2,COLA) 
        elif 'P' in tipo_evento:
            salida_prensado(T,tipo_evento,dicc_camiones,tiempos_molienda,estados_molienda,tiempos_prensado,estados_prensado,tasa2,merma2,tiempos_clarificacion,estados_clarificacion,tasa3)    
        elif 'C' in tipo_evento:
            salida_clarificacion(T,tipo_evento,dicc_camiones,tiempos_prensado,estados_prensado,tiempos_clarificacion,estados_clarificacion,tasa3,merma3)  
        tipo_evento,tiempo_evento=prox_evento(dicc_camiones,tiempos_molienda,tiempos_prensado,tiempos_clarificacion)
    return T,dicc_camiones


In [10]:
dicc_lotes={"lote1":["J1",30000,0.1,2],"lote2":["J2",30000,0.1,2.5],"lote3":["J3",30000,0.1,2.2]}
Simular_procesamiento(dicc_lotes,2,3000,0.05,1,2500,0.15,1,5000,0.1)

INFO CAMIONES: tipo de uva, kg, calidad, tllegada, t en cola, t en molienda,t bloqueado en molienda, t en prensado,t bloqueado en prensado, t en clarif,t bloqueado en clarif, tiempo fuera
{'CAMION1': ['J1', 30000, 0.1, 2, 0, 0, 0, 0, 0, 0, 0, 0], 'CAMION2': ['J2', 30000, 0.1, 2.5, 0, 0, 0, 0, 0, 0, 0, 0], 'CAMION3': ['J3', 30000, 0.1, 2.2, 0, 0, 0, 0, 0, 0, 0, 0]}
{'TSM1': inf, 'TSM2': inf} {'M1': [0, 0], 'M2': [0, 0]}
{'TSP1': inf} {'P1': [0, 0]}
{'TSC1': inf} {'C1': [0, 0]}
[['CAMION1', 2], ['CAMION2', 2.5], ['CAMION3', 2.2], ['TSM1', inf], ['TSM2', inf], ['TSP1', inf], ['TSC1', inf]]
El evento CAMION1 ocurre a las 2 horas
----> Llega el camion CAMION1 a las 2 horas con tipo uva J1, 30000 kg, calidad 0.1.
Se asigna al equipo M1 de molienda. Saldrá en 10.0 horas más.
{'CAMION1': ['J1', 30000, 0.1, inf, 0, 10.0, 0, 0, 0, 0, 0, 2], 'CAMION2': ['J2', 30000, 0.1, 2.5, 0, 0, 0, 0, 0, 0, 0, 0], 'CAMION3': ['J3', 30000, 0.1, 2.2, 0, 0, 0, 0, 0, 0, 0, 0]}
{'M1': [1, 'CAMION1'], 'M2': [0, 0]}


{'C1': [1, 'CAMION3']}
{'TSC1': 120.41443064041918}
vemos si hay equipos en molienda bloqueados
{'M1': [2, 'CAMION2'], 'M2': [2, 'CAMION3']}
{'TSM1': inf, 'TSM2': inf}
camion minimo: CAMION2
Se desbloquea el equipo M1 de molienda. Estuvo bloqueado 110.41402001671938 horas 
Entra al equipo P1 de prensado. Saldra en 0.0009661734113132417 horas mas
{'CAMION1': ['J1', 21802.5, 0.1, inf, 0, 10.0, 0, 11.4, 0, 4.845, 0, 28.244999999999997], 'CAMION2': ['J2', 2.415433528283104, 0.1, inf, 9.5, 10.0, 110.41402001671938, 0.0009661734113132417, 0, 0.0005367630062851342, 0, 120.41359060631434], 'CAMION3': ['J3', 2.0531184990406386, 0.1, inf, 0, 10.0, 110.41305384330806, 0.0009661734113132417, 0, 0.0004106236998081277, 0, 120.41402001671938]}
{'P1': [1, 'CAMION2']}
{'TSP1': 120.41498619013069}
[['CAMION1', inf], ['CAMION2', inf], ['CAMION3', inf], ['TSM1', inf], ['TSM2', inf], ['TSP1', 120.41498619013069], ['TSC1', 120.41443064041918]]
El evento TSC1 ocurre a las 120.41443064041918 horas
<---- Sale 

<---- Sale camion CAMION2 de equipo P1 PRENSADO a las 120.42127618790437 horas con uva tipo J2, 0.00013311459698219636 kg, calidad 0.1
Se asigna al equipo C1 de clarificacion. Saldrá en 2.6622919396439272e-08 horas más.
{'CAMION1': ['J1', 21802.5, 0.1, inf, 0, 10.0, 0, 11.4, 0, 4.845, 0, 28.244999999999997], 'CAMION2': ['J2', 0.00013311459698219636, 0.1, inf, 9.5, 10.0, 110.42127612526221, 6.264216328573945e-08, 0, 2.6622919396439272e-08, 0, 120.42127618790437], 'CAMION3': ['J3', 0.00011980313728397673, 0.1, inf, 0, 10.0, 110.42127606262005, 6.264216328573945e-08, 0, 2.6622919396439272e-08, 0, 120.42127615188512]}
{'C1': [1, 'CAMION2']}
{'TSC1': 120.42127621452728}
vemos si hay equipos en molienda bloqueados
{'M1': [2, 'CAMION2'], 'M2': [2, 'CAMION3']}
{'TSM1': inf, 'TSM2': inf}
camion minimo: CAMION3
Se desbloquea el equipo M2 de molienda. Estuvo bloqueado 110.42127618790437 horas 
Entra al equipo P1 de prensado. Saldra en 4.792125491359069e-08 horas mas
{'CAMION1': ['J1', 21802.5, 0.

{'CAMION1': ['J1', 21802.5, 0.1, inf, 0, 10.0, 0, 11.4, 0, 4.845, 0, 28.244999999999997], 'CAMION2': ['J2', 5.9421182719465525e-09, 0.1, inf, 9.5, 10.0, 110.42127659572701, 2.376847308778621e-12, 0, 1.3204707270992339e-12, 0, 120.42127659572596], 'CAMION3': ['J3', 5.050800531154569e-09, 0.1, inf, 0, 10.0, 110.42127659572463, 2.376847308778621e-12, 0, 1.010160106230914e-12, 0, 120.42127659572701]}
{'P1': [1, 'CAMION2']}
{'TSP1': 120.42127659572938}
[['CAMION1', inf], ['CAMION2', inf], ['CAMION3', inf], ['TSM1', inf], ['TSM2', inf], ['TSP1', 120.42127659572938], ['TSC1', 120.42127659572802]]
El evento TSC1 ocurre a las 120.42127659572802 horas
<---- Sale camion CAMION3 de equipo C1 CLARIFICACION a las 120.42127659572802 horas con uva tipo J3, 4.5457204780391125e-09 kg, calidad 0.1
vemos si hay equipos en prensado bloqueados
{'P1': [1, 'CAMION2']}
{'TSP1': 120.42127659572938}
no hay equipos de prensado bloqueados
[['CAMION1', inf], ['CAMION2', inf], ['CAMION3', inf], ['TSM1', inf], ['TSM2

{'CAMION1': ['J1', 21802.5, 0.1, inf, 0, 10.0, 0, 11.4, 0, 4.845, 0, 28.244999999999997], 'CAMION2': ['J2', 4.784616399653914e-11, 0.1, inf, 9.5, 10.0, 110.4212765957447, 2.5017602089693668e-14, 0, 1.0632480888119808e-14, 0, 120.42127659574474], 'CAMION3': ['J3', 1.5047150272048508e-14, 0.1, inf, 0, 10.0, 110.42127659574473, 1.9138465598615656e-14, 120.42127659574476, 3.0094300544097014e-18, 0, 120.42127659574477]}
{'C1': [1, 'CAMION3']}
{'TSC1': 120.42127659574477}
[['CAMION1', inf], ['CAMION2', inf], ['CAMION3', inf], ['TSM1', inf], ['TSM2', inf], ['TSP1', inf], ['TSC1', 120.42127659574477]]
El evento TSC1 ocurre a las 120.42127659574477 horas
<---- Sale camion CAMION3 de equipo C1 CLARIFICACION a las 120.42127659574477 horas con uva tipo J3, 1.3542435244843657e-14 kg, calidad 0.1
vemos si hay equipos en prensado bloqueados
{'P1': [2, 'CAMION3']}
{'TSP1': inf}
camion minimo: CAMION3
Se desbloquea el equipo P1 de prensado. Estuvo bloqueado 120.42127659574476 horas 
Entra al equipo C1 

...

{'P1': [2, 'CAMION3']}
{'TSP1': inf}
camion minimo: CAMION3
Se desbloquea el equipo P1 de prensado. Estuvo bloqueado 120.42127659574476 horas 
Entra al equipo C1 de clarificacion. Saldra en 1.3923027319646818e-233 horas mas
{'CAMION1': ['J1', 21802.5, 0.1, inf, 0, 10.0, 0, 11.4, 0, 4.845, 0, 28.244999999999997], 'CAMION2': ['J2', 4.784616399653914e-11, 0.1, inf, 9.5, 10.0, 110.4212765957447, 2.5017602089693668e-14, 0, 1.0632480888119808e-14, 0, 120.42127659574474], 'CAMION3': ['J3', 6.961513659823409e-230, 0.1, inf, 0, 10.0, 110.42127659574473, 1.9138465598615656e-14, 120.42127659574476, 1.3923027319646818e-233, 0, 120.42127659574477]}
{'C1': [1, 'CAMION3']}
{'TSC1': 120.42127659574477}
[['CAMION1', inf], ['CAMION2', inf], ['CAMION3', inf], ['TSM1', inf], ['TSM2', inf], ['TSP1', inf], ['TSC1', 120.42127659574477]]
El evento TSC1 ocurre a las 120.42127659574477 horas
<---- Sale camion CAMION3 de equipo C1 CLARIFICACION a las 120.42127659574477 horas con uva tipo J3, 6.265362293841068e-2

vemos si hay equipos en prensado bloqueados
{'P1': [2, 'CAMION3']}
{'TSP1': inf}
camion minimo: CAMION3
Se desbloquea el equipo P1 de prensado. Estuvo bloqueado 120.42127659574476 horas 
Entra al equipo C1 de clarificacion. Saldra en 2.949883371603131e-239 horas mas
{'CAMION1': ['J1', 21802.5, 0.1, inf, 0, 10.0, 0, 11.4, 0, 4.845, 0, 28.244999999999997], 'CAMION2': ['J2', 4.784616399653914e-11, 0.1, inf, 9.5, 10.0, 110.4212765957447, 2.5017602089693668e-14, 0, 1.0632480888119808e-14, 0, 120.42127659574474], 'CAMION3': ['J3', 1.4749416858015655e-235, 0.1, inf, 0, 10.0, 110.42127659574473, 1.9138465598615656e-14, 120.42127659574476, 2.949883371603131e-239, 0, 120.42127659574477]}
{'C1': [1, 'CAMION3']}
{'TSC1': 120.42127659574477}
[['CAMION1', inf], ['CAMION2', inf], ['CAMION3', inf], ['TSM1', inf], ['TSM2', inf], ['TSP1', inf], ['TSC1', 120.42127659574477]]
El evento TSC1 ocurre a las 120.42127659574477 horas
<---- Sale camion CAMION3 de equipo C1 CLARIFICACION a las 120.42127659574477 

{'TSC1': 120.42127659574477}
[['CAMION1', inf], ['CAMION2', inf], ['CAMION3', inf], ['TSM1', inf], ['TSM2', inf], ['TSP1', inf], ['TSC1', 120.42127659574477]]
El evento TSC1 ocurre a las 120.42127659574477 horas
<---- Sale camion CAMION3 de equipo C1 CLARIFICACION a las 120.42127659574477 horas con uva tipo J3, 3.4721902333623464e-241 kg, calidad 0.1
vemos si hay equipos en prensado bloqueados
{'P1': [2, 'CAMION3']}
{'TSP1': inf}
camion minimo: CAMION3
Se desbloquea el equipo P1 de prensado. Estuvo bloqueado 120.42127659574476 horas 
Entra al equipo C1 de clarificacion. Saldra en 6.944380466724693e-245 horas mas
{'CAMION1': ['J1', 21802.5, 0.1, inf, 0, 10.0, 0, 11.4, 0, 4.845, 0, 28.244999999999997], 'CAMION2': ['J2', 4.784616399653914e-11, 0.1, inf, 9.5, 10.0, 110.4212765957447, 2.5017602089693668e-14, 0, 1.0632480888119808e-14, 0, 120.42127659574474], 'CAMION3': ['J3', 3.4721902333623464e-241, 0.1, inf, 0, 10.0, 110.42127659574473, 1.9138465598615656e-14, 120.42127659574476, 6.944380

{'CAMION1': ['J1', 21802.5, 0.1, inf, 0, 10.0, 0, 11.4, 0, 4.845, 0, 28.244999999999997], 'CAMION2': ['J2', 4.784616399653914e-11, 0.1, inf, 9.5, 10.0, 110.4212765957447, 2.5017602089693668e-14, 0, 1.0632480888119808e-14, 0, 120.42127659574474], 'CAMION3': ['J3', 7.356558309689665e-247, 0.1, inf, 0, 10.0, 110.42127659574473, 1.9138465598615656e-14, 120.42127659574476, 1.471311661937933e-250, 0, 120.42127659574477]}
{'C1': [1, 'CAMION3']}
{'TSC1': 120.42127659574477}
[['CAMION1', inf], ['CAMION2', inf], ['CAMION3', inf], ['TSM1', inf], ['TSM2', inf], ['TSP1', inf], ['TSC1', 120.42127659574477]]
El evento TSC1 ocurre a las 120.42127659574477 horas
<---- Sale camion CAMION3 de equipo C1 CLARIFICACION a las 120.42127659574477 horas con uva tipo J3, 6.620902478720699e-247 kg, calidad 0.1
vemos si hay equipos en prensado bloqueados
{'P1': [2, 'CAMION3']}
{'TSP1': inf}
camion minimo: CAMION3
Se desbloquea el equipo P1 de prensado. Estuvo bloqueado 120.42127659574476 horas 
Entra al equipo C1 

KeyboardInterrupt: 